In [ ]:
import numpy as np
import pandas as pd
import copy
from scipy.optimize import linear_sum_assignment, linprog
from matplotlib import pyplot as plt
from matplotlib import collections  as mc

# Exercise of Intro to On-demand and Shared Mobility

<em> prepared by Kenan Zhang; last updated on October 25, 2023</em>

In this exercise, you will play with some simple codes to explore the impact of different factors on matching, trip throughput and vehicle rebalancing.

## Exercise 1: Instant matching vs. batch matching

In the lecture, we discussed two matching methods pair passengers and vehicles as follows:
- instant matching: whenever a passenger arrives, pair it with the closest available driver
- batch matching: collect passengers and vehicles over a matching interval, then solve a linear assignment problem with the objective of minimizing total pickup time

In [ ]:
def generate_agents(n_passengers, n_vehicles, interval_length, side_length):
    """
    Randomly generate passengers and vehicles in a square area, 
    passenger arrival times are spreading over the given time interval
    
    arguments:
        n_passengers (int): number of passengers
        n_vehicles (int): number of vehicles
        interval_length(int): length of time interval
        side_length (int): side length of square area
        
    returns:
        df_passengers (pandas.DataFrame): passenger index, x-y coordinates, arrival time
        df_vehicles (pandas.DataFrame): vehicle index, x-y coordinates
    """
    
    # passengers
    idx = np.arange(n_passengers)  # index
    x = np.random.rand(n_passengers) * side_length  # x-axis
    y = np.random.rand(n_passengers) * side_length  # y-axis
    t = np.random.randint(interval_length, size=n_passengers)  # arrival time
    
    data = np.concatenate((idx, x, y, t)).reshape(4,-1).T
    df_passengers = pd.DataFrame(data=data, columns=['idx','x','y','t'])
    df_passengers.idx = df_passengers.idx.astype(int)
    df_passengers.t = df_passengers.t.astype(int)
    
    
    # vehicles
    idx = np.arange(n_vehicles)  # index
    x = np.random.rand(n_vehicles) * side_length  # x-axis
    y = np.random.rand(n_vehicles) * side_length  # y-axis
    
    data = np.concatenate((idx, x, y)).reshape(3,-1).T 
    df_vehicles = pd.DataFrame(data=data, columns=['idx','x','y'])
    df_vehicles.idx = df_vehicles.idx.astype(int)
    
    
    return df_passengers, df_vehicles
    
    
    

In [ ]:
def instant_matching(df_passengers, df_vehicles):
    """
    Perform instant matching
    
    arguments:
        df_passengers (pandas.DataFrame): passenger index, x-y coordinates, arrival time
        df_vehicles (pandas.DataFrame): vehicle index, x-y coordinates
        
    returns:
        df_matched (pandas.DataFrame): matched passenger id, vehicle id, pickup distance
        df_unmatched (pandas.DataFrame): unmatched passengers
    """
    
    # sort passengers by arrival time
    df_passengers_sort = df_passengers.sort_values(by=['t']).reset_index().drop(columns=['index'])
    
    # init available vehicles
    df_vehicles_available = copy.deepcopy(df_vehicles)
    
    # match passengers one-by-one
    n = min(len(df_passengers), len(df_vehicles))  # number of matches
    data = np.zeros((n, 3))
    for i in range(n):
        id_passenger = df_passengers_sort.idx[i]
        x_passenger = df_passengers_sort.x[i]
        y_passenger = df_passengers_sort.y[i]
        id_vehicle, pickup_distance = search_closest_vehicle(x_passenger, y_passenger, df_vehicles_available)
        df_vehicles_available = df_vehicles_available[df_vehicles_available.idx != id_vehicle].reset_index().drop(columns=['index'])
        data[i] = [id_passenger, id_vehicle, pickup_distance]
    
    # matched trips
    df_matched = pd.DataFrame(data=data, columns=['id_passenger','id_vehicle','pickup_distance'])
    df_matched.id_passenger = df_matched.id_passenger.astype(int)
    df_matched.id_vehicle = df_matched.id_vehicle.astype(int)
    
    # unmatched passengers
    df_unmatched = df_passengers_sort[n:]
    
    return df_matched, df_unmatched
    

def search_closest_vehicle(x_passenger, y_passenger, df_vehicles):
    """
    Search closest vehicle to given passenger based on Euclidean distance
    
    arguments:
        x_passenger (float): x coordinate of passenger location
        y_passenger (float): y coordinate of passenger location
        df_vehicles (pandas.DataFrame): available vehicle index, x-y coordinates
    
    returns:
        id_vehicle (int): index of matched vehicle
        pickup_distance (float): pickup distance
    """
    
    dx = df_vehicles.x - x_passenger
    dy = df_vehicles.y - y_passenger
    distance = np.sqrt(dx**2 + dy**2)
    id_min = np.argmin(distance)
    id_vehicle = df_vehicles.idx[id_min]
    pickup_distance = distance[id_min]
    
    return id_vehicle, pickup_distance

    
    

In [ ]:
def batch_matching(df_passengers, df_vehicles):
    """
    Perform batch matching
    
    arguments:
        df_passengers (pandas.DataFrame): passenger index, x-y coordinates, arrival time
        df_vehicles (pandas.DataFrame): vehicle index, x-y coordinates
        
    returns:
        df_matched (pandas.DataFrame): matched passenger id, vehicle id, pickup distance
        df_unmatched (pandas.DataFrame): unmatched passengers
    """
    
    # compute distance between each pair of passenger and vehicle
    mtx = distance_matrix(df_passengers, df_vehicles)
    
    # solve linear assignment problem
    id_passenger, id_vehicle = linear_sum_assignment(mtx)
    
    # matched trips
    pickup_distance = mtx[id_passenger, id_vehicle]
    data = np.concatenate((id_passenger, id_vehicle, pickup_distance)).reshape(3, -1).T
    df_matched = pd.DataFrame(data=data, columns=['id_passenger','id_vehicle','pickup_distance'])
    df_matched.id_passenger = df_matched.id_passenger.astype(int)
    df_matched.id_vehicle = df_matched.id_vehicle.astype(int)
    
    # unmatched passengers
    match = np.zeros(len(df_passengers))  # binary indicator of matched passengers
    match[id_passenger] = 1 
    df_unmatched = df_passengers[match == 0]
    
    return df_matched, df_unmatched    
    

def distance_matrix(df_passengers, df_vehicles):
    """
    Compute pickup distance between each pair of passenger and vehicle
    
    arguments:
        df_passengers (pandas.DataFrame): passenger index, x-y coordinates, arrival time
        df_vehicles (pandas.DataFrame): vehicle index, x-y coordinates
    
    returns:
        mtx (numpy.array): matrix of pickup distance (row: passenger, column: vehicle)
    
    """
    
    n_passengers = len(df_passengers)
    n_vehicles = len(df_vehicles)
    
    mtx = np.zeros((n_passengers, n_vehicles))
    for i in range(n_passengers):
        x_passenger = df_passengers.x[i]
        y_passenger = df_passengers.y[i]
        dx = df_vehicles.x - x_passenger
        dy = df_vehicles.y - y_passenger
        mtx[i] = np.sqrt(dx**2 + dy**2)
    
    return mtx

In [ ]:
def plot_matching(df_passengers, df_vehicles, df_matched):
    """
    Plot passengers, vehicles and matching
    
    arguments:
        df_passengers (pandas.DataFrame): passenger index, x-y coordinates, arrival time
        df_vehicles (pandas.DataFrame): vehicle index, x-y coordinates
        df_matched (pandas.DataFrame): matched passenger id, vehicle id, pickup distance
    
    returns:
        fig (matplotlib.pyplot.figure): plot
    """
    
    # initiate figure
    fig, ax = plt.subplots(figsize=(6,6))
    
    # plot passengers and drivers
    ax.scatter(df_passengers.x, df_passengers.y, marker='o', label='passenger')
    ax.scatter(df_vehicles.x, df_vehicles.y, marker='^', label='vehicles')
    
    # plot matches
    matches = generate_match_lines(df_passengers, df_vehicles, df_matched)
    ax.add_collection(matches)
    
    # set axis labels and legends
    ax.set_xlabel('x')
    ax.set_ylabel('y')
    ax.legend()
    
    return fig


def generate_match_lines(df_passengers, df_vehicles, df_matched):
    """
    Generate matches as line segments
    
    arguments:
        df_passengers (pandas.DataFrame): passenger index, x-y coordinates, arrival time
        df_vehicles (pandas.DataFrame): vehicle index, x-y coordinates
        df_matched (pandas.DataFrame): matched passenger id, vehicle id, pickup distance
    
    returns:
        matches (matplotlib.collections.LineCollection): matches as line collection
    """
    
    n_matches = len(df_matched)
    cood_passengers = df_passengers.loc[df_matched.id_passenger][['x','y']].values
    cood_vehicles = df_vehicles.loc[df_matched.id_vehicle][['x','y']].values
    lines = [[tuple(cood_passengers[i]), tuple(cood_vehicles[i])] for i in range(n_matches)]
    matches = mc.LineCollection(lines, colors='k', linewidth=1)
    
    return matches
        

In [ ]:
def plot_pickup_distance(varname, var_min, var_max, tt_in_mean, tt_in_std, tt_ba_mean, tt_ba_std):
    """
    Plot total pickup distance with error bars
    
    arguments:
        varname (str): variable name
        var_min (int): min value
        var_max (int): max value 
        tt_in_mean (numpy.array): mean  of total pickup distance by instant matching
        tt_in_std (numpy.array): standard deviation of total pickup distance by instant matching
        tt_ba_mean (numpy.array): mean  of total pickup distance by batch matching
        tt_ba_std (numpy.array): standard  of total pickup distance by batch matching
        
    returns:
        fig (matplotlib.pyplot.figure): plot
    """
    
    fig, ax = plt.subplots()
    x = np.arange(var_min, var_max+1)
    ax.errorbar(x, tt_in_mean, yerr=tt_in_std, capsize=5, label='instant')
    ax.errorbar(x, tt_ba_mean, yerr=tt_ba_std, capsize=5, label='batch')
    
    ax.set_xlabel(varname)
    ax.set_ylabel('total pickup distance')
    ax.legend()
    
    return fig
    

### Plot matching outcomes

Let us first visually compare the outcomes of instant matching and batch matching. Below, we match 10 passengers and 10 vehicles within a square of 5 during time interval of 5. 

In [ ]:
n_passengers = 10
n_vehicles = 10
interval_length = 5
side_length = 5
df_passengers, df_vehicles = generate_agents(n_passengers, n_vehicles, interval_length, side_length)

In [ ]:
# instant matching
df_matched_in, df_unmatched_in = instant_matching(df_passengers, df_vehicles)
fig_in = plot_matching(df_passengers, df_vehicles, df_matched_in)

In [ ]:
# batch matching
df_matched_ba, df_unmatched_ba = batch_matching(df_passengers, df_vehicles)
fig_ba = plot_matching(df_passengers, df_vehicles, df_matched_ba)

Do you find a major difference between the two plots? Which one seems to be more efficient? You may generate several sets of passengers and vehicles to see how the matching outcomes change with passenger and vehicle distributions. 

### Comparison of total pickup distance

Next, let us compare the total pickup distance between the two matching methods and explore how the difference change with major input factors. As an example, we increase the number of passengers while fixing all other parameters. 

In [ ]:
def total_pickup_distance_against_passenger(n_passengers_min, n_passengers_max, n_trials, n_vehicles, interval_length, side_length):
    """
    Total pickup distance against number of passengers 
    
    arguments:
        n_passengers_min (int): min number of passengers
        n_passengers_max (int): max number of passengers
        n_trials (int): number of trials
        intervel_length (int): length of time interval
        side_length (int): side length of square area
        
    returns:
        tt_in_mean (numpy.array): mean  of total pickup distance by instant matching
        tt_in_std (numpy.array): standard deviation of total pickup distance by instant matching
        tt_ba_mean (numpy.array): mean  of total pickup distance by batch matching
        tt_ba_std (numpy.array): standard  of total pickup distance by batch matching
    """
    
    n = n_passengers_max - n_passengers_min + 1
    tt_in = np.zeros((n, n_trials))
    tt_ba = np.zeros((n, n_trials))
    
    for i in range(n):
        n_passengers = n_passengers_min + i
        for j in range(n_trials):
            # generate passengers and vehicles
            df_passengers, df_vehicles = generate_agents(n_passengers, n_vehicles, interval_length, side_length)
            
            # solve instant matching
            df_matched_in, df_unmatched_in = instant_matching(df_passengers, df_vehicles)
            tt_in[i,j] = np.sum(df_matched_in.pickup_distance)
            
            # solve batch matching
            df_matched_ba, df_unmatched_ba = batch_matching(df_passengers, df_vehicles)
            tt_ba[i,j] = np.sum(df_matched_ba.pickup_distance)
    
    
    # compute statistics
    tt_in_mean = np.mean(tt_in, axis=1)
    tt_in_std = np.std(tt_in, axis=1)
    
    tt_ba_mean = np.mean(tt_ba, axis=1)
    tt_ba_std = np.std(tt_ba, axis=1)
            
        
    return tt_in_mean, tt_in_std, tt_ba_mean, tt_ba_std
        
    
    

In [ ]:
# default values
n_passengers = 10
n_vehicles = 10
n_trials = 100
interval_length = 5
side_length = 5

In [ ]:
n_passengers_min = 5
n_passengers_max = 20
tt_in_mean, tt_in_std, tt_ba_mean, tt_ba_std = total_pickup_distance_against_passenger(n_passengers_min, n_passengers_max, n_trials, n_vehicles, interval_length, side_length)

In [ ]:
varname = 'num of passengers'
var_min = n_passengers_min
var_max = n_passengers_max
fig = plot_pickup_distance(varname, var_min, var_max, tt_in_mean, tt_in_std, tt_ba_mean, tt_ba_std)

What can you conclude from the plot? Can you change the function <code>total_pickup_distance_against_passenger</code> to study other variables (i.e., number of vehicles, matching area, and matching interval)?

## Exercise 2: Supply curve of taxi vs. Uber

In the lecture, we discussed the supply curve of Uber, which is derived from the flow conservation.

\begin{equation}
\label{eq:flow-conservation}\tag{1}
N = \Lambda + Q\cdot(w_p+\tau)
\end{equation}

where
- $N$ is the fleet size
- $\Lambda$ is the vacant vehicle density
- $Q$ is the trip throughput
- $w_p$ is the pickup time
- $\tau$ is the average trip duration

Rearranging Eq.\eqref{eq:flow-conservation} and replacing $\Lambda$ by $\Lambda(w_p)$ yields the trip throughput as a function of total waiting time $w=w_m+w_p\approx w_p$:

\begin{equation}
Q(w) = \frac{N-\Lambda(w)}{w+\tau}
\label{eq:supply-uber}\tag{2}
\end{equation}

Taking derivative of Eq.\eqref{eq:supply-uber} with respect to $w$ yields

\begin{equation}
\frac{\partial Q(w)}{\partial w} = - \frac{\Lambda'(w)}{w+\tau} - \frac{N-\Lambda(w)}{(w_p+\tau)^2}
\label{eq:supply-partial-uber}\tag{3}
\end{equation}


According to Arnott's model, 
\begin{equation}
w_p = \frac{k}{2v\sqrt{\Lambda}} \quad \Rightarrow \quad  \Lambda(w_p) = \frac{k^2}{4v^2w_p^2} \quad \Rightarrow \quad  \Lambda'(w_p) = -\frac{k^2}{2v^2w_p^3}
\label{eq:pickup-time-uber}\tag{4}
\end{equation}

Plugging Eq.\eqref{eq:pickup-time-uber} into Eq.\eqref{eq:supply-partial-uber} yields
\begin{equation}
\frac{\partial Q(w)}{\partial w} = \frac{k^2}{2v^2w^3(w+\tau)} - \frac{4Nv^2w^2-k^2}{4v^2w^2(w+\tau)^2}
\label{eq:supply-partial-uber-final}\tag{5}
\end{equation}


Note that both terms in Eq.\eqref{eq:supply-partial-uber-final} are positive, which implies the sign of $\frac{\partial Q(w)}{\partial w}$ may flip at certain value of $w$. The physical meaning is that the trip throughput may not always increase with waiting time $w$. When the market observes fewer trips with longer waiting time, it is said to enter an <em>inefficient equilibrium</em>. 

Similarly, we can derive the supply function of street-hailing taxi. As per Douglas' model, the pickup time is negligible while the matching time can be approximated as $w_m= \frac{k}{v\Lambda}$. Hence, the supply function is given by 

\begin{equation}
Q(w) = \frac{N-\Lambda(w)}{\tau} = \frac{Nvw - k}{vw\tau}
\label{eq:supply-taxi}\tag{6}
\end{equation}

One can easily show that $Q(w)$ is mononotically inceasing with $w$. In other words, street-hailing is free from the paradoxical inefficient equilibrium in Uber. 

In [ ]:
def plot_supply_curves(w_min, w_max, N, v, tau, k_uber, k_taxi):
    """
    Plot supply curves of Uber and taxi
    
    arguments:
        w_min (float): min value of waiting time
        w_max (float): max value of waiting time
        N (int): fleet size
        v (float): vehicle speed
        tau (int): trip duration
        k_uber (float): parameter in Uber pickup time formula
        k_taxi (float): parameter in taxi pickup time formula
    
    returns:
        fig (matplotlib.pyplot.Figure): figure
    
    """
    
    w = np.linspace(w_min, w_max)
    Lambda_uber = (k_uber/(2*v*w))**2
    Lambda_taxi = k_taxi/(v*w)
    
    Q_uber = (N-Lambda_uber)/(w+tau)
    Q_taxi = (N-Lambda_taxi)/tau
    
    fig, ax = plt.subplots()
    ax.plot(w, Q_uber, label='Uber')
    ax.plot(w, Q_taxi, label='taxi')
    ax.set_xlabel('waiting time')
    ax.set_ylabel('trip throughput')
    ax.legend()
    
    return fig

In [ ]:
w_min = 30  # in second
w_max = 300
N = 0.5  # per square meter
v = 3  # meter per second
tau = 600 

k_uber = 100
k_taxi = 50
fig = plot_supply_curves(w_min, w_max, N, v, tau, k_uber, k_taxi)

What can you conclude from the plot? How sensitive is this finding with respect to other parameters (e.g., fleet size and vehicle speed)? Can you write a function to plot $\frac{\partial Q(w)}{\partial w}$ and identify the threshold value of $w$ for an efficient equilibrium in Uber? 

## Exercise 3: Vehicle rebalancing

In the lecture, we formulate a static rebalancing problem:

\begin{align}
\max_{x,x^0} \quad & \sum_{ij} p_{ij}x_{ij} - c_{ij} x^0_{ij}\\
s.t. \quad & x_{ij} = \alpha_{ij} g(\lambda_i, \sum_k (x_{ki}+x^0_{ki})),\\
& \sum_k (x_{ki} + x^0_{ki}) = \sum_j (x_{ij} + x^0_{ij}),\\
& \sum_{ij} (x_{ij} + x^0_{ij})\tau_{ij} = N,\\
& x_{ij}, x^0_{ij}\geq 0.
\end{align}

where 
- $x_{ij}$ and $x^0_{ij}$ are the trip and relocation flows from zone $i$ to zone $j$, respectively
- $p_{ij}$ and $c_{ij}$ are the trip fare and relocation cost from zone $i$ to zone $j$, respectively
- $\lambda_i$ is the demand rate in zone $i$
- $\alpha_{ij}\in[0,1]$ is the fraction of trips from zone $i$ that have destinations in zone $j$ ($sum_j \alpha_{ij}=1$)
- $g(\lambda_i, s_i)$ dictates the number of matched trip in zone $i$ with demand $\lambda_i$ and supply $s_i$
- $\tau_{ij}$ is travel time from zone $i$ to zone$j$
- $N$ is the fleet size


For simplicity, we assume the matching in each zone is frictionless, i.e., $g(\lambda_i, s_i) = \min(\lambda_i, s_i)$. Further, we introduce an auxiliary variable $z$ and reformulate the rebalancing problem into a linear program:

\begin{align}
\max_{x,x^0,z} \quad & \sum_{ij} p_{ij}x_{ij} - c_{ij} x^0_{ij}\\
s.t. \quad & x_{ij} = \alpha_{ij} z_i,\\
& \sum_k (x_{ki} + x^0_{ki}) = \sum_j (x_{ij} + x^0_{ij}),\\
& \sum_{ij} (x_{ij} + x^0_{ij})\tau_{ij} = N,\\
& z_i \leq \lambda_i,\\
& z_i \leq \sum_k (x_{ki}+x^0_{ki}), \\
& x_{ij}, x^0_{ij}, z_i\geq 0.
\end{align}

In [ ]:
def static_rebalancing(n, p, c, lamb, alpha, N, tau):
    """
    Solve static vehicle rebalancing as a linear program
    
    arguments:
        n (int): number of zones
        p (numpy.array): trip fares matrix
        c (numpy.array): relocation cost matrix
        lamb (numpy.array): demand rate vector
        alpha (numpy.array): OD pattern matrix
        fleet size (int): fleet size
        tau (numpy.array): travel time matrix
    
    returns:
        obj (float): objective value at optimal solution
        x (numpy.array): trip flow matrix
        x0 (numpy.array): relocation flow matrix
    
    """
    
    """
    Note: 
        The linprog method in scipy library solve the following linear program
        (https://docs.scipy.org/doc/scipy/reference/generated/scipy.optimize.linprog.html)
        
        min_x  c^T x
        s.t.   A_ub x <= b_ub,
               A_eq x = b_eq,
               l <= x <= u.
    |
        To write our problem in this format, we have
        - x: [x, x0, z]
        - c: [p, -c, 0]
        - A_ub: [0, 0, I; diag(-1), diag(-1), I]
        - b_ub: [lamb, 0]
        - A_eq: [I, 0, -alpha; 
    """
    # cost vector in objective
    co = np.concatenate((-p.reshape(-1), c.reshape(-1), np.zeros(n)))
    
    # inequality constraints
    # 1: z_i <= lamb_i
    A1 = np.concatenate((np.zeros((n, n*n)), np.zeros((n, n*n)), np.eye(n)), axis=1)
    b1 = lamb
    # 2: -sum_k (x_ki + x^0_ki) + z_i <= 0
    A2 = np.concatenate((-np.tile(np.eye(n), n), -np.tile(np.eye(n), n), np.eye(n)), axis=1)
    b2 = np.zeros(n)
    A_ub = np.concatenate((A1, A2), axis=0)
    b_ub = np.concatenate((b1, b2))
    
    # equality constraints
    # 1: x_ij - alpha_ij z_i = 0
    alpha_mtx = (np.repeat(np.eye(n), n, axis=1) * alpha.reshape(-1)).T
    A1 = np.concatenate((np.eye(n*n), np.zeros((n*n, n*n)), -alpha_mtx), axis=1)
    b1 = np.zeros(n*n)
    # 2: sum_k (x_ki + x^0_ki) - sum_j (x_ij + x^0_ij) = 0
    A2 = np.concatenate((np.tile(np.eye(n), n), np.tile(np.eye(n), n), np.zeros((n,n))), axis=1)
    A2 = A2 - np.concatenate((np.repeat(np.eye(n), n, axis=1), np.repeat(np.eye(n), n, axis=1), np.zeros((n,n))), axis=1)
    b2 = np.zeros(n)
    # 3: sum_ij (x_ij + x^0_ij)tau_ij = N
    A3 = np.concatenate((tau.reshape(-1), tau.reshape(-1), np.zeros(n))).reshape(1,-1)
    b3 = [N]
    A_eq = np.concatenate((A1, A2, A3), axis=0)
    b_eq = np.concatenate((b1, b2, b3))
    
    
    # upper/lower bounds
    bounds = [(0, None)] * (n*n + n*n + n)
    
    # solve LP
    lp = linprog(co, A_ub=A_ub, b_ub=b_ub, A_eq=A_eq, b_eq=b_eq, bounds=bounds)
    obj = lp.fun
    sol = lp.x
    
    x = sol[:n*n].reshape(n, n)
    x0 = sol[n*n:2*n*n].reshape(n, n)
    
    return -obj, x, x0

 

In [ ]:
def no_rebalancing(n, p, lamb, alpha, N, tau):
    """
    Stationary results without rebalancing
    
    arguments:
        n (int): number of zones
        p (numpy.array): trip fares matrix
        lamb (numpy.array): demand rate vector
        fleet size (int): fleet size
        tau (numpy.array): travel time matrix
    
    returns:
        returns:
        obj (float): objective value at optimal solution
        x (numpy.array): trip flow matrix
        x0 (numpy.array): relocation flow matrix
    
    """
    
    """
    Note: we solve the same linear program with additional equality constraint x^0_ij = 0, forall i != j
    """
    
    # cost vector in objective
    co = np.concatenate((-p.reshape(-1), np.zeros(n*n), np.zeros(n)))
    
    # inequality constraints
    # 1: z_i <= lamb_i
    A1 = np.concatenate((np.zeros((n, n*n)), np.zeros((n, n*n)), np.eye(n)), axis=1)
    b1 = lamb
    # 2: -sum_k (x_ki + x^0_ki) + z_i <= 0
    A2 = np.concatenate((-np.tile(np.eye(n), n), -np.tile(np.eye(n), n), np.eye(n)), axis=1)
    b2 = np.zeros(n)
    A_ub = np.concatenate((A1, A2), axis=0)
    b_ub = np.concatenate((b1, b2))
    
    # equality constraints
    # 1: x_ij - alpha_ij z_i = 0
    alpha_mtx = (np.repeat(np.eye(n), n, axis=1) * alpha.reshape(-1)).T
    A1 = np.concatenate((np.eye(n*n), np.zeros((n*n, n*n)), -alpha_mtx), axis=1)
    b1 = np.zeros(n*n)
    # 2: sum_k (x_ki + x^0_ki) - sum_j (x_ij + x^0_ij) = 0
    A2 = np.concatenate((np.tile(np.eye(n), n), np.tile(np.eye(n), n), np.zeros((n,n))), axis=1)
    A2 = A2 - np.concatenate((np.repeat(np.eye(n), n, axis=1), np.repeat(np.eye(n), n, axis=1), np.zeros((n,n))), axis=1)
    b2 = np.zeros(n)
    # 3: sum_ij (x_ij + x^0_ij)tau_ij = N
    A3 = np.concatenate((tau.reshape(-1), tau.reshape(-1), np.zeros(n))).reshape(1,-1)
    b3 = [N]
    # 4: x^0_ij = 0, forall i != j
    A4 = np.diag((np.ones((n, n)) - np.eye(n)).reshape(-1))
    A4 = np.concatenate((np.zeros((n*n, n*n)), A4, np.zeros((n*n, n))), axis=1)
    b4 = np.zeros(n*n)
    A_eq = np.concatenate((A1, A2, A3, A4), axis=0)
    b_eq = np.concatenate((b1, b2, b3, b4))
    
    
    # upper/lower bounds
    bounds = [(0, None)] * (n*n + n*n + n)
    
    # solve LP
    lp = linprog(co, A_ub=A_ub, b_ub=b_ub, A_eq=A_eq, b_eq=b_eq, bounds=bounds)
    obj = lp.fun
    sol = lp.x
    
    x = sol[:n*n].reshape(n, n)
    x0 = sol[n*n:2*n*n].reshape(n, n)
    
    return -obj, x, x0

Consider a simple network of four zones shown below and assume
- trip fare is 1 for trips within zones (e.g., 1->1) and between adjacent zones (e.g., 1->2), and 2 for those between diagnal zones (e.g., 1->4)
- relocation cost is 0.5 and 1 for adjacent and diagnal zones, respectively; vehicles staying in the same zone do not induce any cost
- travel time is 1 for trips within zones and between adjacent zones, and 2 for those between diagnal zones, respectively
- demand rate is $\lambda_i=10,\forall i$
- fleet size is 50


In [ ]:
fig, ax = plt.subplots()
node_data = np.array([[0, 1], 
                      [1, 1], 
                      [0, 0], 
                      [1, 0]])

for x, y in node_data:
    ax.plot(x, y, 'o', markersize=40, color='silver')

node_labels = ["1", "2", "3", "4"]
for label, (x, y) in zip(node_labels, node_data):
    ax.text(x, y, label, ha='center', fontsize=15)

for i in range(len(node_data)):
    j = i+1
    while j < len(node_data):
        ax.plot(node_data[[i,j],0], node_data[[i,j],1], color='silver', alpha=0.5)
        j+=1

ax.set_xlim(-0.5, 1.5)
ax.set_ylim(-0.5, 1.5)

ax.set_xticks([])
ax.set_yticks([])

ax.set_xlabel('')
ax.set_ylabel('')
ax.spines['top'].set_visible(False)
ax.spines['right'].set_visible(False)
ax.spines['bottom'].set_visible(False)
ax.spines['left'].set_visible(False)
plt.show()

In [ ]:
# defaut values
n = 4
p = np.array([
    [1, 1, 1, 2],
    [1, 1, 2, 1],
    [1, 2, 1, 1],
    [2, 1, 1, 1]
])

c = (p - np.eye(n)) * 0.5

tau = p
lamb = 10 * np.ones(n)
N = 50

vmin = 0
vmax = 5

### Visualize rebalancing flows

In [ ]:
def plot_rebalancing_flow(n, x0, vmin, vmax):
    """
    Plot rebalancing flows
    
    arguments:
        n (int): number of zones
        x0 (numpy.array): flow matrix
        vmin (float): min value on colorbar
        vmax (float): max value on colorbar
    
    returns:
        fig (matplotlib.pyplot.Figure): plot
    
    """
    
    fig, ax = plt.subplots()
    im = ax.imshow(x0, vmin=vmin, vmax=vmax)
    ax.set_xlabel('destination zone')
    ax.set_ylabel('origin zone')
    ax.set_xticks(np.arange(n))
    ax.set_xticklabels(np.arange(1,n+1))
    ax.set_yticks(np.arange(n))
    ax.set_yticklabels(np.arange(1,n+1))
    fig.colorbar(im)
    
    return fig

#### Base scenario

Let's first examine the base scenario where the demand is uniformly distributed with $\alpha_{ij}=0.25,\forall i,j$. 

In [ ]:
# uniform demang pattern
alpha = 0.25 * np.ones((n,n))

In [ ]:
obj, x, x0 = static_rebalancing(n, p, c, lamb, alpha, N, tau)
fig = plot_rebalancing_flow(n, x0, vmin, vmax)

What can you observe from the rebalancing plot? Why is that? 

#### Central-peripheral demand

Now let's consider a demand pattern where trips originated in zone 1 are uniformly distributed to all zones while those from other zones all end in zone 1. 

In [ ]:
# central-peripheral demand pattern
alpha = np.array([
    [0.25, 0.25, 0.25, 0.25],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0]
])

In [ ]:
obj, x, x0 = static_rebalancing(n, p, c, lamb, alpha, N, tau)
fig = plot_rebalancing_flow(n, x0, vmin, vmax)

What can you observed in this case? Does it make sense? Can you generate other demand patterns and explore the rebalancing flows?

### Benefit of rebalancing

In [ ]:
def plot_profit_against_demand_imbalance(n, p, c, lamb, N, tau):
    """
    Plot profit against level of demand imbalance
    
    arguments:
        n (int): number of zones
        p (numpy.array): trip fares matrix
        c (numpy.array): relocation cost matrix
        lamb (numpy.array): demand rate vector
        fleet size (int): fleet size
        tau (numpy.array): travel time matrix
    
    returns:
        fig (matplotlib.pyplot.Figure): plot
    
    """
    # setup demand pattern
    alpha_base = 1./n * np.ones((n,n))  # alpha value in base scenario
    m = 20  # number of steps
    step = np.linspace(0, 1./n, m)  # step size
    
    # for each demand pattern
    # solve rebalancing and compute profit with and without rebalancing 
    r_wo = np.zeros(m)
    r_w = np.zeros(m)
    for i in range(m):
        alpha = copy.deepcopy(alpha_base)
        alpha[1:,1:] -= step[i]
        alpha[1:,0] += (n-1)*step[i]
        
        r_wo[i], __, __ = no_rebalancing(n, p, lamb, alpha, N, tau)
        r_w[i], __, __ = static_rebalancing(n, p, c, lamb, alpha, N, tau)
        
    
    fig, ax = plt.subplots()
    ax.plot(step, r_wo, label='w/o rebalancing')
    ax.plot(step, r_w, label='w/ rebalancing')
    ax.set_xlabel('demand imbalance level')
    ax.set_ylabel('profit')
    ax.legend()
    
    return fig
    


Now let's explore how rebalancing helps improve the system efficiency. To start with, we make the OD pattern vary from uniform to central-peripheral while keeping other other parameters the same. For each OD pattern, we derive the profit with and without rebalancing. 

In [ ]:
fig = plot_profit_against_demand_imbalance(n, p, c, lamb, N, tau)

What can you conclude from the plot? Can you write a function similar to <code>plot_profit_against_demand_imbalance</code> to explore the benefit of rebalancing with respect to other parameters (e.g., fleet size, rebalancing cose)?